In [1]:
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
from pull_data import pull_JHU_data, pull_UofT_data, pull_GC, aggregate_UofT, update_data_locally

import math
import json

import numpy as np
import pandas as pd

In [344]:
update_data_locally()

In [345]:
df_JHU = pull_JHU_data()

In [346]:
df_GC = pull_GC()

In [347]:
df_UofT = pull_UofT_data()

/opt/anaconda3/envs/plakk/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3254: DtypeWarning:

Columns (10,11) have mixed types.Specify dtype option on import or set low_memory=False.



In [348]:
agg_new,agg_cumulative=aggregate_UofT(df_UofT)

In [349]:
province_pop = pd.read_csv("../data/Canada/population_by_province.csv",sep="\t",header=None,index_col=0)
province_pop.columns=["population"]

In [350]:
df_UofT["date_report"]=pd.to_datetime(df_UofT["date_report"],dayfirst=True)

# Time Series plots

In [351]:
agg_cumulative["Total"]=agg_cumulative.sum(axis=1)
agg_new["Total"]=agg_new.sum(axis=1)

In [352]:
fig = go.Figure(data=go.Scatter(x=agg_cumulative.index, y=agg_cumulative.Total,
                    mode='lines',
                    name='Total Cases'))
fig.update_layout(title='Total number of cases',
                   xaxis_title='Date',
                   yaxis_title='Number of Cases')
fig.show()

In [353]:
fig = go.Figure(data=go.Scatter(x=agg_new.index, y=agg_new.Total,
                    mode='lines',
                    name='New Cases'))
fig.update_layout(title='Number of new cases',
                   xaxis_title='Date',
                   yaxis_title='Number of Cases')
fig.show()

In [354]:
agg_reset=agg_cumulative.drop("Total",axis=1).stack().reset_index().rename(columns={0:"Number_of_cases"})

In [355]:
fig = px.bar(agg_reset, x="date_report", y="Number_of_cases", color = "province", color_discrete_sequence= px.colors.qualitative.Light24)
fig.add_trace(go.Scatter(x=agg_cumulative.index, y=agg_cumulative.Total,
                    mode='lines',
                    name='Total'))
fig.update_layout(legend_orientation="h")
fig.update_layout(legend=dict( y=-0.45))
fig.update_layout(title='Total number of cases',
                   xaxis_title='Date',
                   yaxis_title='Number of Cases')
fig.show()
with open('../plotly/canada_total_cases.json', 'w') as f:
    f.write(fig.to_json())

In [357]:

provinces = sorted(list(agg_reset.province.unique())+["Nunavut"]) 


#province_pop = province_pop.append( pd.DataFrame( { "population" :35874}, index = ["Yukon"]))
sorted_province_pop = sorted(province_pop.to_dict()["population"])

province_rate =  {}
province_cases = {}
province_week = {}
for p,s in zip(provinces, sorted_province_pop):
    x = agg_reset.loc[agg_reset["province"] == p]
    c = list(x.loc[x.Number_of_cases > 50]["Number_of_cases"])
    province_cases[s] = c
    rate = [100000*x/province_pop.to_dict()["population"][s] for x in c]
    province_rate[s] = rate

In [358]:
province_week = {}
for i, (p,r) in enumerate(province_cases.items()): 
    if len(r)>=7 :
        temp = []
        for r0,r7 in zip(r,r[7:]):
            temp.append(100000*(r7-r0)/province_pop.to_dict()["population"][p])
        province_week[p] =  temp
    else:
        province_week[p] =  []

In [359]:

fig = go.Figure()

color = ['#EB89B5', '#5b7bd6','#ff6960', '#d11411', '#00b159', '#00aedb', '#f37735', '#ffc425',
          '#a200ff', '#f47835', '#d41243', '#8ec127', '#feda75', '#fa7e1e', '#962fbf', '#fa9e1e', 
         '#800000', '#FFFF00', '#7D3C98']

#fig.add_trace(go.Scatter(y=total_cases_per_100k,name = "All Quebec", mode = 'lines+markers'))

for (prov, rates), col in zip(province_rate.items(), color):

    fig.add_trace(go.Scatter(y=rates, name = prov, mode = 'lines+markers', line=dict(color=col)))
    


for (r,p), (_, p_w), col in zip(province_rate.items(), province_week.items(), color):
    fig.add_trace(go.Scatter(x =p[7:] , y=province_week[r], name = r, mode = 'lines+markers', line=dict(color=col), visible = False))

fig.update_layout(
    title_text='Exponential Growth by Date', # title of plot
    xaxis_title_text='Days since first Infection', # xaxis label
    yaxis_title_text='Total cases per 100k', # yaxis label

)

fig.update_layout(
    updatemenus=[
        dict(
            #type="buttons",
            direction="down",
            showactive = True,
            #active = 0,
            x=1,
            y=1.5,
            buttons=list([
                dict(label="Growth per Date",
                     method="update",
                     args=[{"visible": [True]*13+ [False]*13},
                           {"title": 'Exponential Growth since First Infection', 
                            "xaxis.title" : 'Days since first infection',
                            "yaxis.title" : 'Cases per 100k (log scale)',
                            "yaxis.type": "linear",
                            "xaxis.type": "linear",
                            "annotations" : [],
                           }]   ),
                dict(label="Growth per total Cases",
                     method="update",
                     args=[{"visible":  [False]*13+ [True]*13},
                           {"title": 'Exponential Growth per total cases',
                            "xaxis.title" : 'Cases per 100k ',
                            "yaxis.title" : 'New Cases per 100k in last week',
                            "yaxis.type": "linear",
                            "xaxis.type": "linear",
                           }]),
                                dict(label="Growth per Date Log Scale",
                     method="update",
                     args=[{"visible": [True]*13+ [False]*13},
                           {"title": 'Exponential Growth since First Infection', 
                            "xaxis.title" : 'Days since first infection',
                            "yaxis.title" : 'Cases per 100k (log scale)',
                            "yaxis.type": "log",
                            "xaxis.type": "linear",
                            "annotations" : [],
                           }]   ),
                dict(label="Growth per total Cases Log Scale",
                     method="update",
                     args=[{"visible":  [False]*13+ [True]*13},
                           {"title": 'Exponential Growth per total cases',
                            "xaxis.title" : 'Cases per 100k (log scale)',
                            "yaxis.title" : 'New Cases per 100k in last week(log scale)',
                            "yaxis.type": "log",
                            "xaxis.type": "log",
                           }]),
            ]),
        )
    ])


fig.update_layout(
    title_text="Exponential",
)
fig.update_layout(legend_orientation="h")
fig.update_layout(legend=dict( y=-0.4))


fig.show()

with open('../plotly/canada_exponential.json', 'w') as f:
    f.write(fig.to_json())

In [17]:
with open("../data/Canada/gpr_000a11g_e.geojson","r") as infile:
    canada = json.load(infile)
    
with open ("../data/Canada/canada.geojson",'r') as infile:
    canada2 = json.load(infile)

In [15]:
agg_reset.head()

date_report                   province  Number_of_cases
0  2020-01-25                    Alberta              0.0
1  2020-01-25           British Columbia              0.0
2  2020-01-25                   Manitoba              0.0
3  2020-01-25              New Brunswick              0.0
4  2020-01-25  Newfoundland and Labrador              0.0

In [360]:
dates = agg_cumulative.index.unique()

lastday_df = agg_reset.loc[agg_reset.date_report == dates[-1]]


lastday_df.province.replace(["Yukon"],["Yukon Territory"],inplace=True)


In [145]:
lastday_df

date_report                   province  Number_of_cases
1272  2020-06-02                    Alberta           7057.0
1273  2020-06-02           British Columbia           2601.0
1274  2020-06-02                   Manitoba            297.0
1275  2020-06-02              New Brunswick            133.0
1276  2020-06-02  Newfoundland and Labrador            261.0
1277  2020-06-02      Northwest Territories              5.0
1278  2020-06-02                Nova Scotia           1057.0
1279  2020-06-02                    Ontario          30194.0
1280  2020-06-02       Prince Edward Island             27.0
1281  2020-06-02                     Quebec          51593.0
1282  2020-06-02               Saskatchewan            646.0
1283  2020-06-02            Yukon Territory             11.0

In [361]:
fig = px.choropleth(lastday_df, geojson=canada2, color="Number_of_cases", locations="province", 
                    featureidkey= "properties.name", color_continuous_scale='Blues',
                    projection= 'conic equidistant'
                   )
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(title='Total Cases by Province')
fig.show()
with open('../plotly/map_Canada.json', 'w') as f:
    f.write(fig.to_json())

In [362]:
per_pop_dict=(lastday_df.set_index("province")["Number_of_cases"]/province_pop["population"]*100000).to_dict()
lastday_df.loc[:,"Case_per_population"] = lastday_df.province.map(per_pop_dict)
#lastday_df

In [363]:
fig = px.choropleth(lastday_df, geojson=canada2, color="Case_per_population", locations="province", 
                    featureidkey= "properties.name", color_continuous_scale='Blues',
                    projection='conic equidistant'
                   )
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(title='Cases per 100 000 inhabitants, by Province')
fig.show()
with open('../plotly/map_Canada_by_pop.json', 'w') as f:
    f.write(fig.to_json())

In [364]:
df_testing = pull_UofT_data("testing")
df_death = pull_JHU_data(kind = "deaths")

In [365]:
dates = df_death.index.unique()
deaths = df_death.loc[df_death.index == dates[-1]]
deaths = deaths.T
deaths = deaths.rename(index={"Yukon": "Yukon Territory"})
deaths = deaths.sort_index()
deaths["deaths"] = deaths["2020-06-10"]
deaths["Deaths per 100k"] = deaths["deaths"]/province_pop.sort_index()["population"]*100000

In [366]:
dates = df_testing.index.unique()
testing = df_testing.loc[df_testing.index == dates[0]]
testing.province.replace(["Yukon"],["Yukon Territory"],inplace=True)
testing = testing.sort_index()

In [367]:
per_pop_dict=(testing.set_index("province")["cumulative_testing"]/province_pop.sort_index()["population"]*100000).to_dict()
testing.loc[:,"Testing_per_100k"] = testing.province.map(per_pop_dict)
testing = testing.set_index("province")
del testing["testing_info"]
del testing["source"]
del testing["province_source"]
del testing["Unnamed: 4"]



In [368]:
lastday_df = lastday_df.set_index("province")
lastday_df = pd.concat([lastday_df,testing, deaths], axis = 1)

In [369]:



fig = go.Figure()

fig.add_trace(go.Scatter(x=lastday_df['Testing_per_100k'],
                                y=lastday_df['Case_per_population'],
                                mode='markers',
                        text=lastday_df.index,
                        marker=dict(color=[0, 1, 2, 3,4,5,6,7,8,9,10,11,12,13])))

fig.add_trace(go.Scatter(x=lastday_df['Testing_per_100k'],
                                y=lastday_df['Deaths per 100k'],
                                mode='markers',
                                marker=dict(color=[0, 1, 2, 3,4,5,6,7,8,9,10,11,12,13]),
                                text=lastday_df.index, visible=False))





fig.update_layout(
    updatemenus=[
        dict(
            #type="buttons",
            direction="down",
            showactive = True,
            #active = 0,
            x=1,
            y=1.1,
            buttons=list([
                dict(label="Cases per Test",
                     method="update",
                     args=[{"visible": [True, False]},
                           {"title": 'Cases vs Testing', 
                            "xaxis.title" : 'Testing per 100k',
                            "yaxis.title" : 'Cases per 100k',
                            "yaxis.type": "linear",
                            "xaxis.type": "linear",
                            "annotations" : [],
                           }]   ),
                dict(label="Deaths per Test",
                     method="update",
                     args=[{"visible":  [False, True]},
                           {"title": 'Deaths vs Testing',
                            "xaxis.title" : 'Testing per 100k',
                            "yaxis.title" : 'Deaths per 100k',
                            "yaxis.type": "linear",
                            "xaxis.type": "linear",
                           }])]))])



fig.update_layout(
    title = "Cases vs Testing",
    xaxis_title_text='Testing per 100k', # xaxis label
    yaxis_title_text='Cases per 100k', # yaxis label

)

fig.show()

with open('../plotly/province_per_testing.json', 'w') as f:
    f.write(fig.to_json())